In [1]:
import glob, os
import fnmatch
import csv
import numpy as np
import cv2
import re
from matplotlib import pyplot as plt


IMG_DIR='D:\Work\HandPose\multiview_hand_pose_dataset_release_v1'
RESIZED_IMG_SIZE=128


def crop_image(image, xmin, ymin, xmax, ymax):
    return image[ymin:ymax, xmin:xmax]

def plot_landmarks(img, points, color, circle_width):
    for (x,y) in points:
        cv2.circle(img, (x, y), circle_width, color, -1)
    plt.imshow(img)

#count = 0
img_train = []
lmarks_train = []
for root, dirnames, filenames in os.walk(IMG_DIR):
    for filename in filenames:
        if filename.endswith('.jpg'):
            #print(filename)
            fname = os.path.join(root, filename)
            pfname = fname.replace('webcam', 'jointsCam')
            pfname = pfname.replace('jpg', 'txt')
            bxname = fname.replace('webcam', 'bbox')
            bxname = bxname.replace('jpg', 'txt')
            print(fname)            
            #print(pfname)
            #print(bxname) 
            
            #get image
            img = cv2.imread(fname)
            img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
            
            #get bbox
            if not os.path.exists(str(bxname)):
                continue
            file = open(str(bxname), "r+")
            lines = file.readlines()
            #print(lines)
            bbox = []
            for line in lines:
                l = line.split(" ")
                #print (int(l[1]))
                bbox.append(int (l[1]))
            #print(bbox)
            #bbox = list(map(int, bbox))
            #bbox = np.array(bbox)
            #print (bbox[0]) 
            if any(n < 0 for n in bbox):
                print("negative bbox")
                continue
            
            #get landmarks
            if not os.path.exists(str(pfname)):
                continue            
            file = open(str(pfname), "r")
            lines = file.readlines()
            lmarks = []
            for line in lines:
                l = line.split(" ")
                lmarks.append(float(l[1]))
                lmarks.append(float(l[2]))
            lmarks = np.array(lmarks)
            #print(lmarks)
            if any(n < 0 for n in lmarks):
                print("negative landmarks")
                continue   
                
            #plot landmarks
            lmarks1 = lmarks.astype(np.int)
            #plot_landmarks(img, lmarks1.reshape(21, 2), (0, 0, 255), 5)

            #Crop image
            img_cropped = crop_image(img, bbox[1], bbox[0], bbox[3], bbox[2])
            
            #adjustlandmarks according to cropping 
            lmarks = lmarks.reshape(21,2)
            lmarks_cropped = lmarks - (bbox[1], bbox[0])
            #plot cropped landmarks
            #plot_landmarks(img_cropped, lmarks_cropped.astype(np.int), (0, 255, 0), 3)
            
            #Resize image (128, 128, 3) for training
            img_resized = cv2.resize(img_cropped, (RESIZED_IMG_SIZE, RESIZED_IMG_SIZE))
            
            #Adjust landmarks according to resized image
            xscale = img_resized.shape[1]/img_cropped.shape[1]
            yscale = img_resized.shape[0]/img_cropped.shape[0]
            lmarks_resized = lmarks_cropped * (xscale, yscale)
            #plot resized image and landmarks
            #plot_landmarks(img_resized, lmarks_resized.astype(np.int), (255, 0, 0), 2)
            
            lmarks_resized = lmarks_resized.reshape(42)
            img_train.append(img_resized)
            lmarks_train.append(lmarks_resized)
 
np.savez('D:\Work\HandPose\data.npz', img=img_train, lmarks=lmarks_train)
        


D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\0_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\0_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\0_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\0_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\100_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\100_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\100_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\100_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\101_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\101_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\101_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\101_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_rel

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\123_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\124_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\124_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\124_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\124_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\125_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\125_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\125_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\125_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\126_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\126_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\126_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dat

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\14_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\150_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\150_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\150_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\150_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\151_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\151_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\151_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\151_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\152_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\152_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\152_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_data

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\177_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\178_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\178_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\178_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\178_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\179_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\179_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\179_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\179_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\17_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\17_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\17_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_datase

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\203_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\204_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\204_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\204_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\204_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\205_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\205_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\205_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\205_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\206_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\206_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_1\206_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dat

...

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\888_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\888_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\889_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\889_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\889_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\889_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\88_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\88_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\88_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\88_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\890_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\890_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\913_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\914_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\914_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\914_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\914_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\915_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\915_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\915_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\915_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\916_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\916_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\916_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dat

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\937_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\937_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\938_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\938_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\938_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\938_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\939_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\939_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\939_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\939_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\93_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\93_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_datas

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\960_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\960_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\960_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\961_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\961_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\961_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\961_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\962_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\962_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\962_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\962_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\963_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dat

D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\984_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\984_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\984_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\985_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\985_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\985_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\985_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\986_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\986_webcam_2.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\986_webcam_3.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\986_webcam_4.jpg
D:\Work\HandPose\multiview_hand_pose_dataset_release_v1\data_9\987_webcam_1.jpg
D:\Work\HandPose\multiview_hand_pose_dat